# Machine Learning on Mushroom Toxicity

### Description of Dataset

This dataset includes 61069 hypothetical mushrooms with caps based on 173 species (353 mushrooms per species). Each mushroom is identified as definitely edible, definitely poisonous, or of unknown edibility and not recommended (the latter class was combined with the poisonous class).

### Variables

One binary class divided in edible=e and poisonous=p (with the latter one also containing mushrooms of unknown edibility).

Twenty remaining variables (n: nominal, m: metrical)
1. cap-diameter (m): float number in cm
2. cap-shape (n): bell=b, conical=c, convex=x, flat=f,
sunken=s, spherical=p, others=o
3. cap-surface (n): fibrous=i, grooves=g, scaly=y, smooth=s,
shiny=h, leathery=l, silky=k, sticky=t,
wrinkled=w, fleshy=e
4. cap-color (n): brown=n, buff=b, gray=g, green=r, pink=p,
purple=u, red=e, white=w, yellow=y, blue=l,
orange=o, black=k
5. does-bruise-bleed (n): bruises-or-bleeding=t,no=f
6. gill-attachment (n): adnate=a, adnexed=x, decurrent=d, free=e,
sinuate=s, pores=p, none=f, unknown=?
7. gill-spacing (n): close=c, distant=d, none=f
8. gill-color (n): see cap-color + none=f
9. stem-height (m): float number in cm
10. stem-width (m): float number in mm
11. stem-root (n): bulbous=b, swollen=s, club=c, cup=u, equal=e,
rhizomorphs=z, rooted=r
12. stem-surface (n): see cap-surface + none=f
13. stem-color (n): see cap-color + none=f
14. veil-type (n): partial=p, universal=u
15. veil-color (n): see cap-color + none=f
16. has-ring (n): ring=t, none=f
17. ring-type (n): cobwebby=c, evanescent=e, flaring=r, grooved=g,
large=l, pendant=p, sheathing=s, zone=z, scaly=y, movable=m, none=f, unknown=?
18. spore-print-color (n): see cap color
19. habitat (n): grasses=g, leaves=l, meadows=m, paths=p, heaths=h,
urban=u, waste=w, woods=d
20. season (n): spring=s, summer=u, autumn=a, winter=w

### Objectives

Identify what features are most commonly associated with poisonous and non-poisonous mushrooms.




## Step 1: Data Cleaning & Preprocessing

In [1]:
# Import packages
import numpy as np 
import pandas as pd 
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")

In [2]:
# Import data
mushrooms = pd.read_csv('Resources/secondary_data_shuffled.csv', sep=';')

In [3]:
# Check the data
mushrooms.head()

class  cap-diameter cap-shape cap-surface cap-color does-bruise-or-bleed  \
0     e          1.26         x           g         y                    f   
1     e         10.32         f           e         b                    f   
2     p          0.92         x           g         p                    f   
3     p          4.27         x         NaN         p                    f   
4     e          3.08         f           s         w                    f   

  gill-attachment gill-spacing gill-color  stem-height  ...  stem-root  \
0               d          NaN          w         5.04  ...        NaN   
1             NaN            c          b         4.68  ...        NaN   
2               a          NaN          p         4.59  ...        NaN   
3               x          NaN          w         4.55  ...        NaN   
4               d            d          w         2.67  ...        NaN   

  stem-surface stem-color veil-type veil-color has-ring ring-type  \
0            t          y       NaN        NaN        f         f   
1          NaN          w       NaN        NaN        t         f   
2            h          k       NaN        NaN        f         f   
3          NaN          w       NaN        NaN        f         f   
4          NaN          w       NaN        NaN        f         f   

  spore-print-color habitat season  
0               NaN       d      a  
1               NaN       d      a  
2               NaN       d      u  
3               NaN       d      a  
4               NaN       m      a  

[5 rows x 21 columns]

In [4]:
# The data must be cleaned, normalized, and standardized prior to modeling 
clean = mushrooms.dropna(axis=1)

## Step 2: Data Exploration & Visualization

In [5]:
clean.head()

class  cap-diameter cap-shape cap-color does-bruise-or-bleed gill-color  \
0     e          1.26         x         y                    f          w   
1     e         10.32         f         b                    f          b   
2     p          0.92         x         p                    f          p   
3     p          4.27         x         p                    f          w   
4     e          3.08         f         w                    f          w   

   stem-height  stem-width stem-color has-ring habitat season  
0         5.04        1.73          y        f       d      a  
1         4.68       19.44          w        t       d      a  
2         4.59        1.15          k        f       d      u  
3         4.55        6.52          w        f       d      a  
4         2.67        5.18          w        f       m      a

In [6]:
clean.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 61069 entries, 0 to 61068
Data columns (total 12 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   class                 61069 non-null  object 
 1   cap-diameter          61069 non-null  float64
 2   cap-shape             61069 non-null  object 
 3   cap-color             61069 non-null  object 
 4   does-bruise-or-bleed  61069 non-null  object 
 5   gill-color            61069 non-null  object 
 6   stem-height           61069 non-null  float64
 7   stem-width            61069 non-null  float64
 8   stem-color            61069 non-null  object 
 9   has-ring              61069 non-null  object 
 10  habitat               61069 non-null  object 
 11  season                61069 non-null  object 
dtypes: float64(3), object(9)
memory usage: 5.6+ MB


In [7]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import classification_report, confusion_matrix, roc_curve, roc_auc_score, balanced_accuracy_score
from sklearn.tree import export_graphviz
from sklearn.metrics import precision_recall_curve, auc
from sklearn.model_selection import cross_val_predict, cross_val_score

In [46]:
labelencoder_clean=LabelEncoder()
for column in clean.columns:
    clean[column] = labelencoder_clean.fit_transform(clean[column])
clean.head()

class  cap-diameter  cap-shape  cap-color  does-bruise-or-bleed  \
0      0            84          6         11                     0   
1      0           990          2          0                     0   
2      1            50          6          7                     0   
3      1           385          6          7                     0   
4      0           266          2         10                     0   

   gill-color  stem-height  stem-width  stem-color  has-ring  habitat  season  
0          10          394         119          12         0        0       0  
1           0          358        1890          11         1        0       0  
2           7          349          61           4         0        0       2  
3          10          345         598          11         0        0       0  
4          10          157         464          11         0        4       0

## Step 3: Predictive Analyses

### Logistic Regression

In [47]:
# Separate the data into labels and features

# Separate the y variable, the labels
y = clean["class"]

# Separate the X variable, the features
X = clean.drop(columns="class")

In [48]:
# Review the y variable Series
y.head()

0    0
1    0
2    1
3    1
4    0
Name: class, dtype: int64

In [49]:
# Review the X variable DataFrame
X.head()

cap-diameter  cap-shape  cap-color  does-bruise-or-bleed  gill-color  \
0            84          6         11                     0          10   
1           990          2          0                     0           0   
2            50          6          7                     0           7   
3           385          6          7                     0          10   
4           266          2         10                     0          10   

   stem-height  stem-width  stem-color  has-ring  habitat  season  
0          394         119          12         0        0       0  
1          358        1890          11         1        0       0  
2          349          61           4         0        0       2  
3          345         598          11         0        0       0  
4          157         464          11         0        4       0

In [50]:
# Check the balance of our target values, O is edible 1 is poisonous
y.value_counts()

1    33888
0    27181
Name: class, dtype: int64

In [51]:
# Import the train_test_learn module
from sklearn.model_selection import train_test_split

# Split the data using train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    y, 
                                                    random_state=1, 
                                                    )
X_train.shape

(45801, 11)

#### Create a Logistic Regression Model with the Original Data
Step 1: Fit a logistic regression model by using the training data (X_train and y_train).

In [52]:
# Import the LogisticRegression module from SKLearn
from sklearn.linear_model import LogisticRegression

# Instantiate the Logistic Regression model
classifier = LogisticRegression(random_state=1)
classifier

# Fit the model using training data
classifier.fit(X_train, y_train)

LogisticRegression(random_state=1)

In [53]:
# Make a prediction using the testing data
predictions = classifier.predict(X_test)

In [54]:
# Print the balanced_accuracy score of the model
print(f"Original Data Accuracy Score: {balanced_accuracy_score(y_test, predictions)}")

Original Data Accuracy Score: 0.5755327206092121


In [55]:
# Generate a confusion matrix for the model
test_matrix = confusion_matrix(y_test, predictions)
print(test_matrix)

[[2709 4086]
 [2098 6375]]


In [56]:
# Print the classification report for the model
testing_report = classification_report(y_test, predictions)
print(testing_report)

              precision    recall  f1-score   support

           0       0.56      0.40      0.47      6795
           1       0.61      0.75      0.67      8473

    accuracy                           0.59     15268
   macro avg       0.59      0.58      0.57     15268
weighted avg       0.59      0.59      0.58     15268



#### Predict a Logistic Regression Model with Over Resampled Training Data

In [57]:
# Import the RandomOverSampler module form imbalanced-learn
from imblearn.over_sampling import RandomOverSampler

# Instantiate the random oversampler model
# # Assign a random_state parameter of 1 to the model
random_state = RandomOverSampler(random_state = 1)

# Fit the original training data to the random_oversampler model
X_oversampler, y_oversampler = random_state.fit_resample(X_train, y_train)

In [58]:
# Count the distinct values of the resampled labels data
y_oversampler.value_counts()

1    25415
0    25415
Name: class, dtype: int64

In [59]:
# Instantiate the Logistic Regression model
# Assign a random_state parameter of 1 to the model
classifier_oversampler = LogisticRegression(random_state=1)
classifier

# Fit the model using the resampled training data
classifier_oversampler.fit(X_oversampler, y_oversampler)

# Make a prediction using the testing data
oversampler_predictions = classifier_oversampler.predict(X_test)

In [60]:
# Print the balanced_accuracy score of the model 
print(f"Original Data Accuracy Score: {balanced_accuracy_score(y_test, oversampler_predictions)}")

Original Data Accuracy Score: 0.5933973708808147


In [61]:
# Generate a confusion matrix for the model
sampler_matrix = confusion_matrix(y_test, oversampler_predictions)
print(sampler_matrix)

[[4024 2771]
 [3435 5038]]


In [62]:
# Print the classification report for the model
sampler_report = classification_report(y_test, oversampler_predictions)
print(testing_report)

              precision    recall  f1-score   support

           0       0.56      0.40      0.47      6795
           1       0.61      0.75      0.67      8473

    accuracy                           0.59     15268
   macro avg       0.59      0.58      0.57     15268
weighted avg       0.59      0.59      0.58     15268



#### Predict a Logistic Regression Model with Under Resampled Training Data

In [63]:
# Import the RandomOverSampler module form imbalanced-learn
from imblearn.under_sampling import RandomUnderSampler

# Instantiate the random oversampler model
# # Assign a random_state parameter of 1 to the model
random_state = RandomUnderSampler(random_state = 1)

# Fit the original training data to the random_oversampler model
X_undersampler, y_undersampler = random_state.fit_resample(X_train, y_train)

In [65]:
# Count the distinct values of the resampled labels data
y_undersampler.value_counts()

0    20386
1    20386
Name: class, dtype: int64

In [66]:
# Instantiate the Logistic Regression model
# Assign a random_state parameter of 1 to the model
classifier_undersampler = LogisticRegression(random_state=1)
classifier

# Fit the model using the resampled training data
classifier_undersampler.fit(X_undersampler, y_undersampler)

# Make a prediction using the testing data
undersampler_predictions = classifier_undersampler.predict(X_test)

In [67]:
# Print the balanced_accuracy score of the model 
print(f"Original Data Accuracy Score: {balanced_accuracy_score(y_test, undersampler_predictions)}")

Original Data Accuracy Score: 0.5921932082752234


In [68]:
# Generate a confusion matrix for the model
undersampler_matrix = confusion_matrix(y_test, undersampler_predictions)
print(undersampler_matrix)

[[4075 2720]
 [3519 4954]]


In [69]:
# Print the classification report for the model
undersampler_report = classification_report(y_test, undersampler_predictions)
print(testing_report)

              precision    recall  f1-score   support

           0       0.56      0.40      0.47      6795
           1       0.61      0.75      0.67      8473

    accuracy                           0.59     15268
   macro avg       0.59      0.58      0.57     15268
weighted avg       0.59      0.59      0.58     15268



### Decision Tree Model 

In [25]:
 # Initial imports
import pandas as pd
from sklearn import tree
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report

# Needed for decision tree visualization
import sys
!{sys.executable} -m pip install pydotplus
import pydotplus
from IPython.display import Image

In [26]:
clean.head()

class  cap-diameter  cap-shape  cap-color  does-bruise-or-bleed  \
0      0            84          6         11                     0   
1      0           990          2          0                     0   
2      1            50          6          7                     0   
3      1           385          6          7                     0   
4      0           266          2         10                     0   

   gill-color  stem-height  stem-width  stem-color  has-ring  habitat  season  
0          10          394         119          12         0        0       0  
1           0          358        1890          11         1        0       0  
2           7          349          61           4         0        0       2  
3          10          345         598          11         0        0       0  
4          10          157         464          11         0        4       0

In [27]:
 # Define features set
X = clean.copy()
X.drop("class", axis=1, inplace=True)
X.head()

cap-diameter  cap-shape  cap-color  does-bruise-or-bleed  gill-color  \
0            84          6         11                     0          10   
1           990          2          0                     0           0   
2            50          6          7                     0           7   
3           385          6          7                     0          10   
4           266          2         10                     0          10   

   stem-height  stem-width  stem-color  has-ring  habitat  season  
0          394         119          12         0        0       0  
1          358        1890          11         1        0       0  
2          349          61           4         0        0       2  
3          345         598          11         0        0       0  
4          157         464          11         0        4       0

In [28]:
 # Define target vector
y = clean["class"].values.reshape(-1, 1)
y[:5]

array([[0],
       [0],
       [1],
       [1],
       [0]])

In [29]:
 # Splitting into Train and Test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=78)

In [30]:
 # Create the StandardScaler instance
scaler = StandardScaler()

In [31]:
# Fit the Standard Scaler with the training data
X_scaler = scaler.fit(X_train)

In [32]:
# Scale the training data
X_train_scaled = X_scaler.transform(X_train)
X_test_scaled = X_scaler.transform(X_test)

In [33]:
 # Create the decision tree classifier instance
model = tree.DecisionTreeClassifier()

In [34]:
# Fit the model
model = model.fit(X_train_scaled, y_train)

In [35]:
 # Making predictions using the testing data
predictions = model.predict(X_test_scaled)

In [36]:
 # Calculating the confusion matrix
cm = confusion_matrix(y_test, predictions)
cm_df = pd.DataFrame(
    cm, index=["Actual 0", "Actual 1"], columns=["Predicted 0", "Predicted 1"]
)

# Calculating the accuracy score
acc_score = accuracy_score(y_test, predictions)

In [37]:
 # Displaying results
print("Confusion Matrix")
display(cm_df)
print(f"Accuracy Score : {acc_score}")
print("Classification Report")
print(classification_report(y_test, predictions))

Confusion Matrix


Predicted 0  Predicted 1
Actual 0         6685          132
Actual 1          126         8325

Accuracy Score : 0.9831019124967252
Classification Report
              precision    recall  f1-score   support

           0       0.98      0.98      0.98      6817
           1       0.98      0.99      0.98      8451

    accuracy                           0.98     15268
   macro avg       0.98      0.98      0.98     15268
weighted avg       0.98      0.98      0.98     15268



In [40]:
 # Create DOT data
import pydotplus 
dot_data = tree.export_graphviz(
    model, out_file=None, feature_names=X.columns, class_names=["0", "1"], filled=True
)

# Draw graph
graph = pydotplus.graph_from_dot_data(dot_data)

Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.599141 to fit

(process:8848): GLib-GIO-WARNING **: 22:27:49.262: Unexpectedly, UWP app `Microsoft.ScreenSketch_11.2303.17.0_x64__8wekyb3d8bbwe' (AUMId `Microsoft.ScreenSketch_8wekyb3d8bbwe!App') supports 29 extensions but has no verbs

(process:8848): GLib-GIO-WARNING **: 22:27:49.378: Unexpectedly, UWP app `Clipchamp.Clipchamp_2.6.2.0_neutral__yxz26nhyzhsrt' (AUMId `Clipchamp.Clipchamp_yxz26nhyzhsrt!App') supports 41 extensions but has no verbs

